# Capstone Project: Create a Customer Segmentation Report for Arvato Financial Services

In this project, you will analyze demographics data for customers of a mail-order sales company in Germany, comparing it against demographics information for the general population. You'll use unsupervised learning techniques to perform customer segmentation, identifying the parts of the population that best describe the core customer base of the company. Then, you'll apply what you've learned on a third dataset with demographics information for targets of a marketing campaign for the company, and use a model to predict which individuals are most likely to convert into becoming customers for the company. The data that you will use has been provided by our partners at Bertelsmann Arvato Analytics, and represents a real-life data science task.

The versions of those two datasets used in this project will include many more features and has not been pre-cleaned. You are also free to choose whatever approach you'd like to analyzing the data rather than follow pre-determined steps. In your work on this project, make sure that you carefully document your steps and decisions, since your main deliverable for this project will be a blog post reporting your findings.

In [163]:
# Check the present working directory
!pwd

/Users/mohanadelemary/Desktop/Uda/Nano_3_Capstone/bertelsmann-arvato-customer-segmentation


### Download the data
If you do not have the required **data/** directory in your workspace, follow the instructions below. Use either one of the methods below. 

**Method 1** <br/>
You must [download this dataset](https://video.udacity-data.com/topher/2024/August/66b9ba05_arvato_data.tar/arvato_data.tar.gz) from the Downloads section in the classroom, and upload it into the workspace. After you upload the tar file to the present working  directory, **/workspace/cd1971 Data Scientist Capstone/Bertelsmann_Arvato Project Workspace/**,  in the Jupyter server, you can open a terminal and the run the following command to extract the dataset from the compressed file. 
```bash
!tar -xzvf arvato_data.tar.gz
```
This command will extract all the contents of arvato_data.tar.gz into the current directory. 

**Method 2** <br/>
Execute the Python code below to download the dataset. 


In [233]:
import requests
import tarfile
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.impute import KNNImputer
from scipy.sparse import csr_matrix, hstack
from sklearn.preprocessing import OneHotEncoder
from sklearn.decomposition import PCA

%matplotlib inline


pd.set_option('display.max_rows', None)  # Show all rows
pd.set_option('display.max_columns', None)  # Show all columns
pd.set_option('display.width', None)  # Automatically adjust width
pd.set_option('display.max_colwidth', None)  



def download_and_extract(url, extract_to='.'):
    """
    Downloads a tar.gz file from a URL and extracts it to a directory.
    Args:
    - url (str): URL of the tar.gz file to download.
    - extract_to (str): Directory path to extract the contents of the tar.gz file.
    """
    # Get the filename from the URL
    filename = url.split('/')[-1]

    # Download the file
    print("Downloading the file...")
    response = requests.get(url, stream=True)
    if response.status_code == 200:
        with open(filename, 'wb') as file:
            file.write(response.raw.read())
        print("Download completed.")
    else:
        print("Failed to download the file.")
        return

    # Extract the tar.gz file
    print("Extracting the file...")
    try:
        with tarfile.open(filename, 'r:gz') as tar:
            tar.extractall(path=extract_to)
        print("Extraction completed.")
    except Exception as e:
        print(f"Failed to extract the file: {e}")
    finally:
        # Optionally remove the tar.gz file after extraction
        os.remove(filename)
        print("Downloaded tar.gz file removed.")

# URL of the tar.gz file
url = 'https://video.udacity-data.com/topher/2024/August/66b9ba05_arvato_data.tar/arvato_data.tar.gz'

# Call the function with the URL
download_and_extract(url)




### Important Note
>Delete the **data/** folder and the downloaded tar file, before you submit your code. The current workspace cannot save the files beyond 1GB of space in total. 


### Import the Packages

## Part 0: Get to Know the Data

There are four data files associated with this project:

- `Udacity_AZDIAS_052018.csv`: Demographics data for the general population of Germany; 891 211 persons (rows) x 366 features (columns).
- `Udacity_CUSTOMERS_052018.csv`: Demographics data for customers of a mail-order company; 191 652 persons (rows) x 369 features (columns).
- `Udacity_MAILOUT_052018_TRAIN.csv`: Demographics data for individuals who were targets of a marketing campaign; 42 982 persons (rows) x 367 (columns).
- `Udacity_MAILOUT_052018_TEST.csv`: Demographics data for individuals who were targets of a marketing campaign; 42 833 persons (rows) x 366 (columns).

Each row of the demographics files represents a single person, but also includes information outside of individuals, including information about their household, building, and neighborhood. Use the information from the first two files to figure out how customers ("CUSTOMERS") are similar to or differ from the general population at large ("AZDIAS"), then use your analysis to make predictions on the other two files ("MAILOUT"), predicting which recipients are most likely to become a customer for the mail-order company.

The "CUSTOMERS" file contains three extra columns ('CUSTOMER_GROUP', 'ONLINE_PURCHASE', and 'PRODUCT_GROUP'), which provide broad information about the customers depicted in the file. The original "MAILOUT" file included one additional column, "RESPONSE", which indicated whether or not each recipient became a customer of the company. For the "TRAIN" subset, this column has been retained, but in the "TEST" subset it has been removed; it is against that withheld column that your final predictions will be assessed in the Kaggle competition.

Otherwise, all of the remaining columns are the same between the three data files. For more information about the columns depicted in the files, you can refer to two Excel spreadsheets provided in the workspace. [One of them](./DIAS Information Levels - Attributes 2017.xlsx) is a top-level list of attributes and descriptions, organized by informational category. [The other](./DIAS Attributes - Values 2017.xlsx) is a detailed mapping of data values for each feature in alphabetical order.

In the below cell, we've provided some initial code to load in the first two datasets. Note for all of the `.csv` data files in this project that they're semicolon (`;`) delimited, so an additional argument in the [`read_csv()`](https://pandas.pydata.org/pandas-docs/stable/generated/pandas.read_csv.html) call has been included to read in the data properly. Also, considering the size of the datasets, it may take some time for them to load completely.

You'll notice when the data is loaded in that a warning message will immediately pop up. Before you really start digging into the modeling and analysis, you're going to need to perform some cleaning. Take some time to browse the structure of the data and look over the informational spreadsheets to understand the data values. Make some decisions on which features to keep, which features to drop, and if any revisions need to be made on data formats. It'll be a good idea to create a function with pre-processing steps, since you'll need to clean all of the datasets before you work with them.

>Note: If you experience "Kernel died" issue while running the codeblock below, then load less number of rows from the .csv files.

In [234]:
# load in the data
azdias = pd.read_csv('Udacity_AZDIAS_052018.csv', sep=';')
customers = pd.read_csv('Udacity_CUSTOMERS_052018.csv', sep=';')

/var/folders/df/vskq6r65025_c31r_18tdcpr0000gn/T/ipykernel_63399/2693282953.py:2: DtypeWarning: Columns (18,19) have mixed types. Specify dtype option on import or set low_memory=False.
  azdias = pd.read_csv('Udacity_AZDIAS_052018.csv', sep=';')
/var/folders/df/vskq6r65025_c31r_18tdcpr0000gn/T/ipykernel_63399/2693282953.py:3: DtypeWarning: Columns (18,19) have mixed types. Specify dtype option on import or set low_memory=False.
  customers = pd.read_csv('Udacity_CUSTOMERS_052018.csv', sep=';')


### Part 0.1: Attributes Dictionary

We'll read in the two files explaining our features and values for reference and to understand how to interpret the population and customers data

In [235]:
#Reading in the two files explaining our attributes and values
attributes_values = pd.read_excel('DIAS Attributes - Values 2017.xlsx')
info = pd.read_excel('DIAS Information Levels - Attributes 2017.xlsx')

In [236]:
info.head(20)

Unnamed: 0         Unnamed: 1             Unnamed: 2  \
0          NaN  Information level              Attribute   
1          NaN                NaN               AGER_TYP   
2          NaN             Person   ALTERSKATEGORIE_GROB   
3          NaN                NaN              ANREDE_KZ   
4          NaN                NaN          CJT_GESAMTTYP   
5          NaN                NaN      FINANZ_MINIMALIST   
6          NaN                NaN          FINANZ_SPARER   
7          NaN                NaN       FINANZ_VORSORGER   
8          NaN                NaN         FINANZ_ANLEGER   
9          NaN                NaN  FINANZ_UNAUFFAELLIGER   
10         NaN                NaN       FINANZ_HAUSBAUER   
11         NaN                NaN              FINANZTYP   
12         NaN                NaN            GEBURTSJAHR   
13         NaN                NaN        GFK_URLAUBERTYP   
14         NaN                NaN       GREEN_AVANTGARDE   
15         NaN                NaN             HEALTH_TYP   
16         NaN                NaN    LP_LEBENSPHASE_FEIN   
17         NaN                NaN    LP_LEBENSPHASE_GROB   
18         NaN                NaN        LP_FAMILIE_FEIN   
19         NaN                NaN        LP_FAMILIE_GROB   

                                                                                          Unnamed: 3  \
0                                                                                        Description   
1                                                                                 best-ager typology   
2                                                                      age through prename analysis    
3                                                                                             gender   
4   Customer-Journey-Typology relating to the preferred information and buying channels of consumers   
5                                                         financial typology: low financial interest   
6                                                                    financial typology: money saver   
7                                                                    financial typology: be prepared   
8                                                                       financial typology: investor   
9                                                                   financial typology: unremarkable   
10                                                   financial typology: main focus is the own house   
11                                                      best descirbing financial type for the peron   
12                                                                                     year of birth   
13                                                                                   vacation habits   
14       the environmental sustainability is the dominating movement in the youth of these consumers   
15                                                                                   health typology   
16                                                                                    lifestage fine   
17                                                                                   lifestage rough   
18                                                                                  family type fine   
19                                                                                 family type rough   

                                                                                                                                                                                                                                           Unnamed: 4  
0                                                                                                                                                                                                                                    Additional notes  
1                                                             

In [237]:
attributes_values.head()

Unnamed: 0 Unnamed: 1          Unnamed: 2 Unnamed: 3  \
0         NaN  Attribute         Description      Value   
1         NaN   AGER_TYP  best-ager typology         -1   
2         NaN        NaN                 NaN          0   
3         NaN        NaN                 NaN          1   
4         NaN        NaN                 NaN          2   

                   Unnamed: 4  
0                     Meaning  
1                     unknown  
2  no classification possible  
3             passive elderly  
4            cultural elderly

In [238]:
# Setting up the proper column names for attributes_values
attributes_values.columns = attributes_values.iloc[0]    # Set first row as header
attributes_values = attributes_values[1:].reset_index(drop=True)   # Drop the first row and reset index
attributes_values.head()

0  NaN Attribute         Description Value                     Meaning
0  NaN  AGER_TYP  best-ager typology    -1                     unknown
1  NaN       NaN                 NaN     0  no classification possible
2  NaN       NaN                 NaN     1             passive elderly
3  NaN       NaN                 NaN     2            cultural elderly
4  NaN       NaN                 NaN     3   experience-driven elderly

In [239]:
# Columns Attribute & Description seem to have the key values at their first row.
# Subsequent rows contain the other values possible for the same attribute. 
# Therefore we simply need to forward-fill these columns

columns_to_fill = ['Attribute', 'Description']
attributes_values[columns_to_fill] = attributes_values[columns_to_fill].fillna(method='ffill')
attributes_values.head()

/var/folders/df/vskq6r65025_c31r_18tdcpr0000gn/T/ipykernel_63399/402792525.py:6: FutureWarning: DataFrame.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  attributes_values[columns_to_fill] = attributes_values[columns_to_fill].fillna(method='ffill')


0  NaN Attribute         Description Value                     Meaning
0  NaN  AGER_TYP  best-ager typology    -1                     unknown
1  NaN  AGER_TYP  best-ager typology     0  no classification possible
2  NaN  AGER_TYP  best-ager typology     1             passive elderly
3  NaN  AGER_TYP  best-ager typology     2            cultural elderly
4  NaN  AGER_TYP  best-ager typology     3   experience-driven elderly

In [240]:
# Setting up the proper column names for info

info.columns = info.iloc[0]    # Set first row as header
info = info[1:].reset_index(drop=True)   # Drop the first row and reset index
info.head()

0  NaN Information level             Attribute  \
0  NaN               NaN              AGER_TYP   
1  NaN            Person  ALTERSKATEGORIE_GROB   
2  NaN               NaN             ANREDE_KZ   
3  NaN               NaN         CJT_GESAMTTYP   
4  NaN               NaN     FINANZ_MINIMALIST   

0                                                                                       Description  \
0                                                                                best-ager typology   
1                                                                     age through prename analysis    
2                                                                                            gender   
3  Customer-Journey-Typology relating to the preferred information and buying channels of consumers   
4                                                        financial typology: low financial interest   

0                                                                                                                                                                                                                                   Additional notes  
0                                                                                                                                                                         in cooperation with Kantar TNS; the information basis is a consumer survey  
1                                                                                                                                                                                            modelled on millions of first name-age-reference data    
2                                                                                                                                                                                                                                                NaN  
3  relating to the preferred information, marketing and buying channels of consumers as well as their cross-channel usage. The information basis is a survey on the consumer channel preferences combined via a statistical modell with AZ DIAS data  
4                                                                                                                                        Gfk-Typology based on a representative household panel combined via a statistical modell with AZ DIAS data

In [241]:
# Removing the Null column at the beginning of the attributes_values df

attributes_values = attributes_values.iloc[:, 1:]
info = info.iloc[:, 1:]
attributes_values.head()

0 Attribute         Description Value                     Meaning
0  AGER_TYP  best-ager typology    -1                     unknown
1  AGER_TYP  best-ager typology     0  no classification possible
2  AGER_TYP  best-ager typology     1             passive elderly
3  AGER_TYP  best-ager typology     2            cultural elderly
4  AGER_TYP  best-ager typology     3   experience-driven elderly

In [242]:
# Joining both df's into a single df on the attribute column

attributes = info.merge(attributes_values, how='outer', on='Attribute')
attributes.head()

0 Information level Attribute       Description_x  \
0               NaN  AGER_TYP  best-ager typology   
1               NaN  AGER_TYP  best-ager typology   
2               NaN  AGER_TYP  best-ager typology   
3               NaN  AGER_TYP  best-ager typology   
4               NaN  AGER_TYP  best-ager typology   

0                                                            Additional notes  \
0  in cooperation with Kantar TNS; the information basis is a consumer survey   
1  in cooperation with Kantar TNS; the information basis is a consumer survey   
2  in cooperation with Kantar TNS; the information basis is a consumer survey   
3  in cooperation with Kantar TNS; the information basis is a consumer survey   
4  in cooperation with Kantar TNS; the information basis is a consumer survey   

0       Description_y Value                     Meaning  
0  best-ager typology    -1                     unknown  
1  best-ager typology     0  no classification possible  
2  best-ager typology     1             passive elderly  
3  best-ager typology     2            cultural elderly  
4  best-ager typology     3   experience-driven elderly

In [243]:
# The information level column is mostly nulls. very little cells with values

attributes['Information level'].value_counts()

Information level
Household             22
Microcell (RR4_ID)    10
Postcode               8
125m x 125m Grid       8
PLZ8                   7
Person                 6
Microcell (RR3_ID)     6
RR1_ID                 5
Building               1
Community              1
Name: count, dtype: int64

In [244]:
attributes.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2271 entries, 0 to 2270
Data columns (total 7 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   Information level  74 non-null     object
 1   Attribute          2271 non-null   object
 2   Description_x      2176 non-null   object
 3   Additional notes   173 non-null    object
 4   Description_y      2258 non-null   object
 5   Value              2258 non-null   object
 6   Meaning            2247 non-null   object
dtypes: object(7)
memory usage: 124.3+ KB


In [245]:
def fetch_contains(search_string, df=attributes, ):

    """
    PURPOSE:
    - Provide a quick way to query and understand any attribute that we'll be working with in the population and customer data
    
    INPUT: 
    - Search_string: String of characters to look for in all cells of a dataframe
    - df: specifies the dataframe to query, by default it is the attributes dataframe
    
    OUTPUT:
    - dataframe containing all rows where the string queried was found
    
    """
    # Create a mask that checks for substring containment
    mask = df.apply(lambda row: row.astype(str).str.contains(search_string, case=False, na=False).any(), axis=1)

    # Use the mask with query
    result = attributes[mask]

    return result

In [246]:
fetch_contains('ager')

0    Information level        Attribute              Description_x  \
0                  NaN         AGER_TYP         best-ager typology   
1                  NaN         AGER_TYP         best-ager typology   
2                  NaN         AGER_TYP         best-ager typology   
3                  NaN         AGER_TYP         best-ager typology   
4                  NaN         AGER_TYP         best-ager typology   
89                 NaN   CAMEO_DEU_2015  CAMEO_4.0: specific group   
105                NaN   CAMEO_DEU_2015  CAMEO_4.0: specific group   
736                NaN  GFK_URLAUBERTYP            vacation habits   
1906               NaN  LP_FAMILIE_FEIN           family type fine   
1909               NaN  LP_FAMILIE_FEIN           family type fine   
1980               NaN   LP_STATUS_FEIN        social status fine    

0                                                               Additional notes  \
0     in cooperation with Kantar TNS; the information basis is a consumer survey   
1     in cooperation with Kantar TNS; the information basis is a consumer survey   
2     in cooperation with Kantar TNS; the information basis is a consumer survey   
3     in cooperation with Kantar TNS; the information basis is a consumer survey   
4     in cooperation with Kantar TNS; the information basis is a consumer survey   
89                                                                           NaN   
105                                                                          NaN   
736                                                                          NaN   
1906                                                                         NaN   
1909                                                                         NaN   
1980                                                                         NaN   

0                                            Description_y Value  \
0                                       best-ager typology    -1   
1                                       best-ager typology     0   
2                                       best-ager typology     1   
3                                       best-ager typology     2   
4                                       best-ager typology     3   
89    CAMEO classification 2015 - detailled classification    1B   
105   CAMEO classification 2015 - detailled classification    4E   
736                                        vacation habits     7   
1906                                        familytyp fine     4   
1909                                        familytyp fine     7   
1980                                    social status fine     4   

0                         Meaning  
0                         unknown  
1      no classification possible  
2                 passive elderly  
3                cultural elderly  
4       experience-driven elderly  
89              Wealthy Best Ager  
105                   Golden Ager  
736                   Golden ager  
1906  single parent with teenager  
1909        family with teenager   
1980                    villagers

### Part 0.2: Customers & Population Data 

Given that the dataframes are closely related and will be compared to each other in the end, it makes sense to do the analysis and cleaning for both in parallel


In [247]:
azdias.head()

LNR  AGER_TYP  AKT_DAT_KL  ALTER_HH  ALTER_KIND1  ALTER_KIND2  \
0  910215        -1         NaN       NaN          NaN          NaN   
1  910220        -1         9.0       0.0          NaN          NaN   
2  910225        -1         9.0      17.0          NaN          NaN   
3  910226         2         1.0      13.0          NaN          NaN   
4  910241        -1         1.0      20.0          NaN          NaN   

   ALTER_KIND3  ALTER_KIND4  ALTERSKATEGORIE_FEIN  ANZ_HAUSHALTE_AKTIV  \
0          NaN          NaN                   NaN                  NaN   
1          NaN          NaN                  21.0                 11.0   
2          NaN          NaN                  17.0                 10.0   
3          NaN          NaN                  13.0                  1.0   
4          NaN          NaN                  14.0                  3.0   

   ANZ_HH_TITEL  ANZ_KINDER  ANZ_PERSONEN  ANZ_STATISTISCHE_HAUSHALTE  \
0           NaN         NaN           NaN                         NaN   
1           0.0         0.0           2.0                        12.0   
2           0.0         0.0           1.0                         7.0   
3           0.0         0.0           0.0                         2.0   
4           0.0         0.0           4.0                         3.0   

   ANZ_TITEL  ARBEIT  BALLRAUM CAMEO_DEU_2015 CAMEO_DEUG_2015 CAMEO_INTL_2015  \
0        NaN     NaN       NaN            NaN             NaN             NaN   
1        0.0     3.0       6.0             8A             8.0            51.0   
2        0.0     3.0       2.0             4C             4.0            24.0   
3        0.0     2.0       4.0             2A             2.0            12.0   
4        0.0     4.0       2.0             6B             6.0            43.0   

   CJT_GESAMTTYP  CJT_KATALOGNUTZER  CJT_TYP_1  CJT_TYP_2  CJT_TYP_3  \
0            2.0                5.0        1.0        1.0        5.0   
1            5.0                1.0        5.0        5.0        2.0   
2            3.0                2.0        4.0        4.0        1.0   
3            2.0                3.0        2.0        2.0        4.0   
4            5.0                3.0        3.0        3.0        3.0   

   CJT_TYP_4  CJT_TYP_5  CJT_TYP_6  D19_BANKEN_ANZ_12  D19_BANKEN_ANZ_24  \
0        5.0        5.0        5.0                  0                  0   
1        3.0        1.0        1.0                  0                  0   
2        3.0        2.0        2.0                  0                  0   
3        4.0        5.0        3.0                  0                  0   
4        4.0        3.0        3.0                  3                  5   

   D19_BANKEN_DATUM  D19_BANKEN_DIREKT  D19_BANKEN_GROSS  D19_BANKEN_LOKAL  \
0                10                  0                 0                 0   
1                10                  0                 0                 0   
2                10                  0                 0                 0   
3                10                  0                 0                 0   
4                 5                  1                 2                 0   

   D19_BANKEN_OFFLINE_DATUM  D19_BANKEN_ONLINE_DATUM  \
0                        10                       10   
1                        10                       10   
2                        10                       10   
3                        10                       10   
4                        10                        5   

   D19_BANKEN_ONLINE_QUOTE_12  D19_BANKEN_REST  D19_BEKLEIDUNG_GEH  \
0                         NaN                0                   0   
1                         NaN                0                   0   
2                         0.0                0                   0   
3                         0.0                0                   0   
4                        10.0                6                   6   

   D19_BEKLEIDUNG_REST  D19_BILDUNG  D19_BIO_OEKO  D19_BUCH_CD  \
0                    0   

In [248]:
customers.head()

LNR  AGER_TYP  AKT_DAT_KL  ALTER_HH  ALTER_KIND1  ALTER_KIND2  \
0    9626         2         1.0      10.0          NaN          NaN   
1    9628        -1         9.0      11.0          NaN          NaN   
2  143872        -1         1.0       6.0          NaN          NaN   
3  143873         1         1.0       8.0          NaN          NaN   
4  143874        -1         1.0      20.0          NaN          NaN   

   ALTER_KIND3  ALTER_KIND4  ALTERSKATEGORIE_FEIN  ANZ_HAUSHALTE_AKTIV  \
0          NaN          NaN                  10.0                  1.0   
1          NaN          NaN                   NaN                  NaN   
2          NaN          NaN                   0.0                  1.0   
3          NaN          NaN                   8.0                  0.0   
4          NaN          NaN                  14.0                  7.0   

   ANZ_HH_TITEL  ANZ_KINDER  ANZ_PERSONEN  ANZ_STATISTISCHE_HAUSHALTE  \
0           0.0         0.0           2.0                         1.0   
1           NaN         0.0           3.0                         NaN   
2           0.0         0.0           1.0                         1.0   
3           NaN         0.0           0.0                         1.0   
4           0.0         0.0           4.0                         7.0   

   ANZ_TITEL  ARBEIT  BALLRAUM CAMEO_DEU_2015 CAMEO_DEUG_2015 CAMEO_INTL_2015  \
0        0.0     1.0       3.0             1A             1.0            13.0   
1        0.0     NaN       NaN            NaN             NaN             NaN   
2        0.0     3.0       7.0             5D             5.0            34.0   
3        0.0     1.0       7.0             4C             4.0            24.0   
4        0.0     3.0       3.0             7B             7.0            41.0   

   CJT_GESAMTTYP  CJT_KATALOGNUTZER  CJT_TYP_1  CJT_TYP_2  CJT_TYP_3  \
0            5.0                4.0        1.0        1.0        5.0   
1            NaN                NaN        NaN        NaN        NaN   
2            2.0                5.0        2.0        2.0        5.0   
3            2.0                5.0        1.0        1.0        5.0   
4            6.0                4.0        3.0        3.0        3.0   

   CJT_TYP_4  CJT_TYP_5  CJT_TYP_6  D19_BANKEN_ANZ_12  D19_BANKEN_ANZ_24  \
0        5.0        5.0        5.0                  0                  0   
1        NaN        NaN        NaN                  0                  1   
2        5.0        5.0        5.0                  0                  0   
3        5.0        5.0        5.0                  0                  0   
4        4.0        3.0        3.0                  1                  2   

   D19_BANKEN_DATUM  D19_BANKEN_DIREKT  D19_BANKEN_GROSS  D19_BANKEN_LOKAL  \
0                10                  0                 0                 0   
1                 6                  0                 5                 0   
2                10                  0                 0                 0   
3                10                  0                 0                 0   
4                 3                  5                 0                 3   

   D19_BANKEN_OFFLINE_DATUM  D19_BANKEN_ONLINE_DATUM  \
0                        10                       10   
1                        10                       10   
2                        10                       10   
3                        10                       10   
4                        10                        7   

   D19_BANKEN_ONLINE_QUOTE_12  D19_BANKEN_REST  D19_BEKLEIDUNG_GEH  \
0                         0.0                0                   0   
1                         0.0                6                   0   
2                         0.0                0                   0   
3                         0.0                0                   0   
4                         0.0                0                   0   

   D19_BEKLEIDUNG_REST  D19_BILDUNG  D19_BIO_OEKO  D19_BUCH_CD  \
0                    0   

In [249]:
# Looking into the df's shapes
print(azdias.shape)
print(customers.shape)

(891221, 366)
(191652, 369)


In [250]:
# Checking for duplicates
print(azdias.duplicated().sum())
print(customers.duplicated().sum())

0
0


In [316]:
# Feature selection: We have a lot of financial behaviour data on individual level
# Car purchase behaviour has an extensive amount of columns.
# We'll remove them to refine our features model.


# Filter for columns containing 'KBA_05' or 'KBA_13'
azdias_columns_to_drop = azdias.filter(regex='KBA').columns
customers_columns_to_drop = customers.filter(regex='KBA').columns

# Drop the filtered columns from the DataFrame
azdias = azdias.drop(columns=azdias_columns_to_drop)
customers = customers.drop(columns=customers_columns_to_drop)

# We'll drop two more columns
# CAMEO_DEU_2015 has a very detailed classification while the CAMEO_DEUG_2015 provides a more high-level classification that should
# be sufficient for our needs. CAMEO_DEU_2015 processing would be very demanding

# EINGEFUEGT_AM is just the date of row entry, unnecessary for our analysis

# Drop columns from the DataFrame
azdias = azdias.drop(columns=['CAMEO_DEU_2015','EINGEFUEGT_AM'])
customers = customers.drop(columns=['CAMEO_DEU_2015','EINGEFUEGT_AM'])

In [332]:
customers['CAMEO_DEUG_2015'].dtype

dtype('O')

In [328]:
customers['CAMEO_INTL_2015'].value_counts()

CAMEO_INTL_2015
14      14708
24      13301
41       8461
43       7158
25       6900
15       6845
51       5987
13       5728
22       5566
14.0     4939
24.0     4504
23       4276
34       3945
45       3936
54       3537
41.0     2859
55       2794
12       2791
43.0     2476
25.0     2472
15.0     2372
44       2144
51.0     2126
31       2050
13.0     1955
22.0     1941
35       1741
23.0     1494
34.0     1423
45.0     1352
54.0     1258
32       1256
33       1178
12.0      924
55.0      920
52        770
44.0      688
31.0      681
35.0      553
32.0      440
33.0      396
52.0      253
XX        126
Name: count, dtype: int64

In [333]:
# Replace NaN, 'X', and 'XX' with -1 in specified columns
customers[['CAMEO_DEUG_2015', 'CAMEO_INTL_2015']] = customers[['CAMEO_DEUG_2015', 'CAMEO_INTL_2015']].replace({'X': -1, 'XX': -1}).fillna(-1)
azdias[['CAMEO_DEUG_2015', 'CAMEO_INTL_2015']] = azdias[['CAMEO_DEUG_2015', 'CAMEO_INTL_2015']].replace({'X': -1, 'XX': -1}).fillna(-1)


In [334]:
customers[['CAMEO_DEUG_2015', 'CAMEO_INTL_2015']] = customers[['CAMEO_DEUG_2015', 'CAMEO_INTL_2015']].astype(int)
azdias[['CAMEO_DEUG_2015', 'CAMEO_INTL_2015']] = azdias[['CAMEO_DEUG_2015', 'CAMEO_INTL_2015']].astype(int)

In [337]:
customers['D19_LETZTER_KAUF_BRANCHE'].value_counts()

D19_LETZTER_KAUF_BRANCHE
D19_UNBEKANNT             31910
D19_SONSTIGE              14540
D19_VERSICHERUNGEN        10534
D19_BUCH_CD               10038
D19_VOLLSORTIMENT          8647
D19_HAUS_DEKO              8129
D19_SCHUHE                 6317
D19_BEKLEIDUNG_GEH         5975
D19_DROGERIEARTIKEL        5528
D19_ENERGIE                4454
D19_BEKLEIDUNG_REST        4096
D19_VERSAND_REST           3619
D19_BANKEN_DIREKT          3466
D19_LEBENSMITTEL           3053
D19_TELKO_REST             2303
D19_NAHRUNGSERGAENZUNG     2253
D19_TELKO_MOBILE           2131
D19_TECHNIK                1836
D19_BANKEN_GROSS           1684
D19_FREIZEIT               1672
D19_SAMMELARTIKEL          1610
D19_RATGEBER               1519
D19_KINDERARTIKEL          1439
D19_WEIN_FEINKOST          1424
D19_BANKEN_REST            1233
D19_BIO_OEKO                808
D19_REISEN                  666
D19_DIGIT_SERV              653
D19_GARTEN                  568
D19_HANDWERK                532
D19_BILDUNG    

In [338]:
customers['D19_LETZTER_KAUF_BRANCHE'].isna().sum()

47697

In [339]:
customers['OST_WEST_KZ'].isna().sum()

49927

In [340]:
customers['OST_WEST_KZ'].value_counts()

OST_WEST_KZ
W    130382
O     11343
Name: count, dtype: int64

In [341]:
customers['D19_LETZTER_KAUF_BRANCHE'] = customers['D19_LETZTER_KAUF_BRANCHE'].fillna('D19_UNBEKANNT')

In [ ]:
1. drop column CAMEO_DEU_2015, EINGEFUEGT_AM - DONE
2. Replace nan, X, XX with -1 (CAMEO_DEUG_2015,CAMEO_INTL_2015)- DONE
3. Change to int (CAMEO_DEUG_2015,CAMEO_INTL_2015)- DONE
4. Replace nan(str) with NULL (D19_LETZTER_KAUF_BRANCHE, OST_WEST_KZ)

In [342]:
# Looking into the df's shapes
print(azdias.shape)
print(customers.shape)

(891221, 177)
(191652, 180)


In [343]:
# Checking for Nulls
# To support the analysis of each feature independently, we'll create a function that creates a df with features and Null values for each df

def create_null_table(df):

    """
    INPUT: 
    df: dataframe to be processed

    OUTPUT:
    null_df: dataframe of all the df's columns with the null values within each column and the null% out of all rows if df.
    
    
    """
    null_df = df.isna().sum()
    null_df = null_df.reset_index()
    null_df = null_df.sort_values(by=0,ascending=False)
    null_df.columns = ['feature', 'null_count']

    null_df['percentage'] = null_df['null_count']/(df.shape[0])

    return null_df
    




In [344]:
cn = create_null_table(customers)

In [345]:
an = create_null_table(azdias)


In [346]:
customers.shape

(191652, 180)

In [347]:
cn.head(10)

feature  null_count  percentage
128          OST_WEST_KZ       49927    0.260509
0                    LNR           0    0.000000
123          MOBI_RASTER           0    0.000000
115          KONSUMZELLE           0    0.000000
116      LP_FAMILIE_FEIN           0    0.000000
117      LP_FAMILIE_GROB           0    0.000000
118  LP_LEBENSPHASE_FEIN           0    0.000000
119  LP_LEBENSPHASE_GROB           0    0.000000
120       LP_STATUS_FEIN           0    0.000000
121       LP_STATUS_GROB           0    0.000000

In [348]:
azdias.shape

(891221, 177)

In [349]:
an.head(10)

feature  null_count  percentage
56   D19_LETZTER_KAUF_BRANCHE      257113    0.288495
128               OST_WEST_KZ       93148    0.104517
121            LP_STATUS_GROB           0    0.000000
113                KOMBIALTER           0    0.000000
114               KONSUMNAEHE           0    0.000000
115               KONSUMZELLE           0    0.000000
116           LP_FAMILIE_FEIN           0    0.000000
117           LP_FAMILIE_GROB           0    0.000000
118       LP_LEBENSPHASE_FEIN           0    0.000000
119       LP_LEBENSPHASE_GROB           0    0.000000

In [350]:
# Based on the values for the top six columns in both tables ['ALTER_KIND4','ALTER_KIND3','ALTER_KIND2','ALTER_KIND1','EXTSEL992','KK_KUNDENTYP']
# More than 50% of the columns for these features are nulls in both tables. Dropping them would be the best tactic

azdias.drop(columns=['ALTER_KIND4','ALTER_KIND3','ALTER_KIND2','ALTER_KIND1','EXTSEL992','KK_KUNDENTYP'], inplace=True)
customers.drop(columns=['ALTER_KIND4','ALTER_KIND3','ALTER_KIND2','ALTER_KIND1','EXTSEL992','KK_KUNDENTYP'], inplace=True)


KeyError: "['ALTER_KIND4', 'ALTER_KIND3', 'ALTER_KIND2', 'ALTER_KIND1', 'EXTSEL992', 'KK_KUNDENTYP'] not found in axis"

In [351]:
# re-running the create_null_table function to get updated tables
cn = create_null_table(customers)
an = create_null_table(azdias)

In [352]:
customers.shape

(191652, 180)

In [353]:
cn.head(100)

feature  null_count  percentage
128               OST_WEST_KZ       49927    0.260509
0                         LNR           0    0.000000
123               MOBI_RASTER           0    0.000000
115               KONSUMZELLE           0    0.000000
116           LP_FAMILIE_FEIN           0    0.000000
117           LP_FAMILIE_GROB           0    0.000000
118       LP_LEBENSPHASE_FEIN           0    0.000000
119       LP_LEBENSPHASE_GROB           0    0.000000
120            LP_STATUS_FEIN           0    0.000000
121            LP_STATUS_GROB           0    0.000000
122          MIN_GEBAEUDEJAHR           0    0.000000
124                MOBI_REGIO           0    0.000000
113                KOMBIALTER           0    0.000000
125          NATIONALITAET_KZ           0    0.000000
126         ONLINE_AFFINITAET           0    0.000000
127               ORTSGR_KLS9           0    0.000000
129                PLZ8_ANTG1           0    0.000000
130                PLZ8_ANTG2           0    0.000000
131                PLZ8_ANTG3           0    0.000000
132                PLZ8_ANTG4           0    0.000000
133               PLZ8_BAUMAX           0    0.000000
114               KONSUMNAEHE           0    0.000000
112                       KKK           0    0.000000
1                    AGER_TYP           0    0.000000
111                INNENSTADT           0    0.000000
92       EINGEZOGENAM_HH_JAHR           0    0.000000
93                   EWDICHTE           0    0.000000
94             FINANZ_ANLEGER           0    0.000000
95           FINANZ_HAUSBAUER           0    0.000000
96          FINANZ_MINIMALIST           0    0.000000
97              FINANZ_SPARER           0    0.000000
98      FINANZ_UNAUFFAELLIGER           0    0.000000
99           FINANZ_VORSORGER           0    0.000000
100                 FINANZTYP           0    0.000000
101              FIRMENDICHTE           0    0.000000
102               GEBAEUDETYP           0    0.000000
103        GEBAEUDETYP_RASTER           0    0.000000
104               GEBURTSJAHR           0    0.000000
105               GEMEINDETYP           0    0.000000
106           GFK_URLAUBERTYP           0    0.000000
107          GREEN_AVANTGARDE           0    0.000000
108                HEALTH_TYP           0    0.000000
109             HH_DELTA_FLAG           0    0.000000
110        HH_EINKOMMEN_SCORE           0    0.000000
134                  PLZ8_GBZ           0    0.000000
135                  PLZ8_HHZ           0    0.000000
136     PRAEGENDE_JUGENDJAHRE           0    0.000000
137                  REGIOTYP           0    0.000000
160                  TITEL_KZ           0    0.000000
161                UMFELD_ALT           0    0.000000
162               UMFELD_JUNG           0    0.000000
163          UNGLEICHENN_FLAG           0    0.000000
164          VERDICHTUNGSRAUM           0    0.000000
165                  VERS_TYP           0    0.000000
166                       VHA           0    0.000000
167                       VHN           0    0.000000
168                  VK_DHT4A           0    0.000000
169                VK_DISTANZ           0    0.000000
170                   VK_ZG11           0    0.000000
171            W_KEIT_KIND_HH           0    0.000000
172            WOHNDAUER_2008           0    0.000000
173                  WOHNLAGE           0    0.000000
174                  ZABEOTYP           0    0.000000
175             PRODUCT_GROUP           0    0.000000
176            CUSTOMER_GROUP           0    0.000000
177           ONLINE_PURCHASE           0    0.000000
178                 ANREDE_KZ           0    0.000000
159               STRUKTURTYP           0    0.000000
158                   SOHO_KZ           0    0.000000
157               SHOPPER_TYP           0    0.000000
146                SEMIO_KAEM           0    0.000000
138                  RELAT_AB           0    0.000000
139            RETOURTYP_BK_S           0    0.000000
140            RT_KEIN_ANR

In [354]:
an.head(30)

feature  null_count  percentage
56   D19_LETZTER_KAUF_BRANCHE      257113    0.288495
128               OST_WEST_KZ       93148    0.104517
121            LP_STATUS_GROB           0    0.000000
113                KOMBIALTER           0    0.000000
114               KONSUMNAEHE           0    0.000000
115               KONSUMZELLE           0    0.000000
116           LP_FAMILIE_FEIN           0    0.000000
117           LP_FAMILIE_GROB           0    0.000000
118       LP_LEBENSPHASE_FEIN           0    0.000000
119       LP_LEBENSPHASE_GROB           0    0.000000
120            LP_STATUS_FEIN           0    0.000000
0                         LNR           0    0.000000
132                PLZ8_ANTG4           0    0.000000
122          MIN_GEBAEUDEJAHR           0    0.000000
123               MOBI_RASTER           0    0.000000
124                MOBI_REGIO           0    0.000000
125          NATIONALITAET_KZ           0    0.000000
126         ONLINE_AFFINITAET           0    0.000000
127               ORTSGR_KLS9           0    0.000000
129                PLZ8_ANTG1           0    0.000000
130                PLZ8_ANTG2           0    0.000000
112                       KKK           0    0.000000
111                INNENSTADT           0    0.000000
110        HH_EINKOMMEN_SCORE           0    0.000000
99           FINANZ_VORSORGER           0    0.000000
91                   DSL_FLAG           0    0.000000
92       EINGEZOGENAM_HH_JAHR           0    0.000000
93                   EWDICHTE           0    0.000000
94             FINANZ_ANLEGER           0    0.000000
95           FINANZ_HAUSBAUER           0    0.000000

In [355]:
cdt = customers.dtypes.reset_index()
cdt.columns = ['feature', 'dtype']
cdt[cdt['dtype']!='object']

feature    dtype
0                            LNR    int64
1                       AGER_TYP    int64
2                     AKT_DAT_KL  float64
3                       ALTER_HH  float64
4           ALTERSKATEGORIE_FEIN  float64
5            ANZ_HAUSHALTE_AKTIV  float64
6                   ANZ_HH_TITEL  float64
7                     ANZ_KINDER  float64
8                   ANZ_PERSONEN  float64
9     ANZ_STATISTISCHE_HAUSHALTE  float64
10                     ANZ_TITEL  float64
11                        ARBEIT  float64
12                      BALLRAUM  float64
13               CAMEO_DEUG_2015    int64
14               CAMEO_INTL_2015    int64
15                 CJT_GESAMTTYP  float64
16             CJT_KATALOGNUTZER  float64
17                     CJT_TYP_1  float64
18                     CJT_TYP_2  float64
19                     CJT_TYP_3  float64
20                     CJT_TYP_4  float64
21                     CJT_TYP_5  float64
22                     CJT_TYP_6  float64
23             D19_BANKEN_ANZ_12    int64
24             D19_BANKEN_ANZ_24    int64
25              D19_BANKEN_DATUM    int64
26             D19_BANKEN_DIREKT    int64
27              D19_BANKEN_GROSS    int64
28              D19_BANKEN_LOKAL    int64
29      D19_BANKEN_OFFLINE_DATUM    int64
30       D19_BANKEN_ONLINE_DATUM    int64
31    D19_BANKEN_ONLINE_QUOTE_12  float64
32               D19_BANKEN_REST    int64
33            D19_BEKLEIDUNG_GEH    int64
34           D19_BEKLEIDUNG_REST    int64
35                   D19_BILDUNG    int64
36                  D19_BIO_OEKO    int64
37                   D19_BUCH_CD    int64
38                D19_DIGIT_SERV    int64
39           D19_DROGERIEARTIKEL    int64
40                   D19_ENERGIE    int64
41                  D19_FREIZEIT    int64
42                    D19_GARTEN    int64
43             D19_GESAMT_ANZ_12    int64
44             D19_GESAMT_ANZ_24    int64
45              D19_GESAMT_DATUM    int64
46      D19_GESAMT_OFFLINE_DATUM    int64
47       D19_GESAMT_ONLINE_DATUM    int64
48    D19_GESAMT_ONLINE_QUOTE_12  float64
49                  D19_HANDWERK    int64
50                 D19_HAUS_DEKO    int64
51             D19_KINDERARTIKEL    int64
52                 D19_KONSUMTYP  float64
53             D19_KONSUMTYP_MAX    int64
54                  D19_KOSMETIK    int64
55              D19_LEBENSMITTEL    int64
57                     D19_LOTTO  float64
58        D19_NAHRUNGSERGAENZUNG    int64
59                  D19_RATGEBER    int64
60                    D19_REISEN    int64
61             D19_SAMMELARTIKEL    int64
62                    D19_SCHUHE    int64
63                  D19_SONSTIGE    int64
64                  D19_SOZIALES  float64
65                   D19_TECHNIK    int64
66              D19_TELKO_ANZ_12    int64
67              D19_TELKO_ANZ_24    int64
68               D19_TELKO_DATUM    int64
69              D19_TELKO_MOBILE    int64
70       D19_TELKO_OFFLINE_DATUM    int64
71        D19_TELKO_ONLINE_DATUM    int64
72     D19_TELKO_ONLINE_QUOTE_12  float64
73                D19_TELKO_REST    int64
74               D19_TIERARTIKEL    int64
75            D19_VERSAND_ANZ_12    int64
76            D19_VERSAND_ANZ_24    int64
77             D19_VERSAND_DATUM    int64
78     D19_VERSAND_OFFLINE_DATUM    int64
79      D19_VERSAND_ONLINE_DATUM    int64
80   D19_VERSAND_ONLINE_QUOTE_12  float64
81              D19_VERSAND_REST    int64
82              D19_VERSI_ANZ_12    int64
83              D19_VERSI_ANZ_24    int64
84               D19_VERSI_DATUM    int64
85       D19_VERSI_OFFLINE_DATUM    int64
86        D19_VERSI_ONLINE_DATUM    int64
87     D19_VERSI_ONLINE_QUOTE_12  float64
88            D19_VERSICHERUNGEN    int64
89             D19_VOLLSORTIMENT    int64
90             D19_WEIN_FEINKOST    int64
91                      DSL_FLAG  float64
92          EINGEZOGENAM_HH_JAHR  float64
93                      EWDICHTE  float64
94                FINANZ_ANLEGER    int64
95              FINANZ_HAUSBAUER   

In [356]:
adt = azdias.dtypes.reset_index()
adt.columns = ['feature', 'dtype']
adt[adt['dtype']!='object']

feature    dtype
0                            LNR    int64
1                       AGER_TYP    int64
2                     AKT_DAT_KL  float64
3                       ALTER_HH  float64
4           ALTERSKATEGORIE_FEIN  float64
5            ANZ_HAUSHALTE_AKTIV  float64
6                   ANZ_HH_TITEL  float64
7                     ANZ_KINDER  float64
8                   ANZ_PERSONEN  float64
9     ANZ_STATISTISCHE_HAUSHALTE  float64
10                     ANZ_TITEL  float64
11                        ARBEIT  float64
12                      BALLRAUM  float64
13               CAMEO_DEUG_2015    int64
14               CAMEO_INTL_2015    int64
15                 CJT_GESAMTTYP  float64
16             CJT_KATALOGNUTZER  float64
17                     CJT_TYP_1  float64
18                     CJT_TYP_2  float64
19                     CJT_TYP_3  float64
20                     CJT_TYP_4  float64
21                     CJT_TYP_5  float64
22                     CJT_TYP_6  float64
23             D19_BANKEN_ANZ_12    int64
24             D19_BANKEN_ANZ_24    int64
25              D19_BANKEN_DATUM    int64
26             D19_BANKEN_DIREKT    int64
27              D19_BANKEN_GROSS    int64
28              D19_BANKEN_LOKAL    int64
29      D19_BANKEN_OFFLINE_DATUM    int64
30       D19_BANKEN_ONLINE_DATUM    int64
31    D19_BANKEN_ONLINE_QUOTE_12  float64
32               D19_BANKEN_REST    int64
33            D19_BEKLEIDUNG_GEH    int64
34           D19_BEKLEIDUNG_REST    int64
35                   D19_BILDUNG    int64
36                  D19_BIO_OEKO    int64
37                   D19_BUCH_CD    int64
38                D19_DIGIT_SERV    int64
39           D19_DROGERIEARTIKEL    int64
40                   D19_ENERGIE    int64
41                  D19_FREIZEIT    int64
42                    D19_GARTEN    int64
43             D19_GESAMT_ANZ_12    int64
44             D19_GESAMT_ANZ_24    int64
45              D19_GESAMT_DATUM    int64
46      D19_GESAMT_OFFLINE_DATUM    int64
47       D19_GESAMT_ONLINE_DATUM    int64
48    D19_GESAMT_ONLINE_QUOTE_12  float64
49                  D19_HANDWERK    int64
50                 D19_HAUS_DEKO    int64
51             D19_KINDERARTIKEL    int64
52                 D19_KONSUMTYP  float64
53             D19_KONSUMTYP_MAX    int64
54                  D19_KOSMETIK    int64
55              D19_LEBENSMITTEL    int64
57                     D19_LOTTO  float64
58        D19_NAHRUNGSERGAENZUNG    int64
59                  D19_RATGEBER    int64
60                    D19_REISEN    int64
61             D19_SAMMELARTIKEL    int64
62                    D19_SCHUHE    int64
63                  D19_SONSTIGE    int64
64                  D19_SOZIALES  float64
65                   D19_TECHNIK    int64
66              D19_TELKO_ANZ_12    int64
67              D19_TELKO_ANZ_24    int64
68               D19_TELKO_DATUM    int64
69              D19_TELKO_MOBILE    int64
70       D19_TELKO_OFFLINE_DATUM    int64
71        D19_TELKO_ONLINE_DATUM    int64
72     D19_TELKO_ONLINE_QUOTE_12  float64
73                D19_TELKO_REST    int64
74               D19_TIERARTIKEL    int64
75            D19_VERSAND_ANZ_12    int64
76            D19_VERSAND_ANZ_24    int64
77             D19_VERSAND_DATUM    int64
78     D19_VERSAND_OFFLINE_DATUM    int64
79      D19_VERSAND_ONLINE_DATUM    int64
80   D19_VERSAND_ONLINE_QUOTE_12  float64
81              D19_VERSAND_REST    int64
82              D19_VERSI_ANZ_12    int64
83              D19_VERSI_ANZ_24    int64
84               D19_VERSI_DATUM    int64
85       D19_VERSI_OFFLINE_DATUM    int64
86        D19_VERSI_ONLINE_DATUM    int64
87     D19_VERSI_ONLINE_QUOTE_12  float64
88            D19_VERSICHERUNGEN    int64
89             D19_VOLLSORTIMENT    int64
90             D19_WEIN_FEINKOST    int64
91                      DSL_FLAG  float64
92          EINGEZOGENAM_HH_JAHR  float64
93                      EWDICHTE  float64
94                FINANZ_ANLEGER    int64
95              FINANZ_HAUSBAUER   

In [357]:
fetch_contains('wohnlage')

0    Information level Attribute  \
2248               NaN  WOHNLAGE   
2249               NaN  WOHNLAGE   
2250               NaN  WOHNLAGE   
2251               NaN  WOHNLAGE   
2252               NaN  WOHNLAGE   
2253               NaN  WOHNLAGE   
2254               NaN  WOHNLAGE   
2255               NaN  WOHNLAGE   
2256               NaN  WOHNLAGE   

0                                                Description_x  \
2248  neighbourhood-area (very good -> rather poor; rural nbh)   
2249  neighbourhood-area (very good -> rather poor; rural nbh)   
2250  neighbourhood-area (very good -> rather poor; rural nbh)   
2251  neighbourhood-area (very good -> rather poor; rural nbh)   
2252  neighbourhood-area (very good -> rather poor; rural nbh)   
2253  neighbourhood-area (very good -> rather poor; rural nbh)   
2254  neighbourhood-area (very good -> rather poor; rural nbh)   
2255  neighbourhood-area (very good -> rather poor; rural nbh)   
2256  neighbourhood-area (very good -> rather poor; rural nbh)   

0    Additional notes      Description_y Value  \
2248              NaN  residential-area     -1   
2249              NaN  residential-area      0   
2250              NaN  residential-area      1   
2251              NaN  residential-area      2   
2252              NaN  residential-area      3   
2253              NaN  residential-area      4   
2254              NaN  residential-area      5   
2255              NaN  residential-area      7   
2256              NaN  residential-area      8   

0                                 Meaning  
2248                              unknown  
2249                  no score calculated  
2250              very good neighbourhood  
2251                   good neighbourhood  
2252                average neighbourhood  
2253                   poor neighbourhood  
2254              very poor neighbourhood  
2255                  rural neighbourhood  
2256  new building in rural neighbourhood

In [358]:
cdt[cdt['dtype']!='object']

feature    dtype
0                            LNR    int64
1                       AGER_TYP    int64
2                     AKT_DAT_KL  float64
3                       ALTER_HH  float64
4           ALTERSKATEGORIE_FEIN  float64
5            ANZ_HAUSHALTE_AKTIV  float64
6                   ANZ_HH_TITEL  float64
7                     ANZ_KINDER  float64
8                   ANZ_PERSONEN  float64
9     ANZ_STATISTISCHE_HAUSHALTE  float64
10                     ANZ_TITEL  float64
11                        ARBEIT  float64
12                      BALLRAUM  float64
13               CAMEO_DEUG_2015    int64
14               CAMEO_INTL_2015    int64
15                 CJT_GESAMTTYP  float64
16             CJT_KATALOGNUTZER  float64
17                     CJT_TYP_1  float64
18                     CJT_TYP_2  float64
19                     CJT_TYP_3  float64
20                     CJT_TYP_4  float64
21                     CJT_TYP_5  float64
22                     CJT_TYP_6  float64
23             D19_BANKEN_ANZ_12    int64
24             D19_BANKEN_ANZ_24    int64
25              D19_BANKEN_DATUM    int64
26             D19_BANKEN_DIREKT    int64
27              D19_BANKEN_GROSS    int64
28              D19_BANKEN_LOKAL    int64
29      D19_BANKEN_OFFLINE_DATUM    int64
30       D19_BANKEN_ONLINE_DATUM    int64
31    D19_BANKEN_ONLINE_QUOTE_12  float64
32               D19_BANKEN_REST    int64
33            D19_BEKLEIDUNG_GEH    int64
34           D19_BEKLEIDUNG_REST    int64
35                   D19_BILDUNG    int64
36                  D19_BIO_OEKO    int64
37                   D19_BUCH_CD    int64
38                D19_DIGIT_SERV    int64
39           D19_DROGERIEARTIKEL    int64
40                   D19_ENERGIE    int64
41                  D19_FREIZEIT    int64
42                    D19_GARTEN    int64
43             D19_GESAMT_ANZ_12    int64
44             D19_GESAMT_ANZ_24    int64
45              D19_GESAMT_DATUM    int64
46      D19_GESAMT_OFFLINE_DATUM    int64
47       D19_GESAMT_ONLINE_DATUM    int64
48    D19_GESAMT_ONLINE_QUOTE_12  float64
49                  D19_HANDWERK    int64
50                 D19_HAUS_DEKO    int64
51             D19_KINDERARTIKEL    int64
52                 D19_KONSUMTYP  float64
53             D19_KONSUMTYP_MAX    int64
54                  D19_KOSMETIK    int64
55              D19_LEBENSMITTEL    int64
57                     D19_LOTTO  float64
58        D19_NAHRUNGSERGAENZUNG    int64
59                  D19_RATGEBER    int64
60                    D19_REISEN    int64
61             D19_SAMMELARTIKEL    int64
62                    D19_SCHUHE    int64
63                  D19_SONSTIGE    int64
64                  D19_SOZIALES  float64
65                   D19_TECHNIK    int64
66              D19_TELKO_ANZ_12    int64
67              D19_TELKO_ANZ_24    int64
68               D19_TELKO_DATUM    int64
69              D19_TELKO_MOBILE    int64
70       D19_TELKO_OFFLINE_DATUM    int64
71        D19_TELKO_ONLINE_DATUM    int64
72     D19_TELKO_ONLINE_QUOTE_12  float64
73                D19_TELKO_REST    int64
74               D19_TIERARTIKEL    int64
75            D19_VERSAND_ANZ_12    int64
76            D19_VERSAND_ANZ_24    int64
77             D19_VERSAND_DATUM    int64
78     D19_VERSAND_OFFLINE_DATUM    int64
79      D19_VERSAND_ONLINE_DATUM    int64
80   D19_VERSAND_ONLINE_QUOTE_12  float64
81              D19_VERSAND_REST    int64
82              D19_VERSI_ANZ_12    int64
83              D19_VERSI_ANZ_24    int64
84               D19_VERSI_DATUM    int64
85       D19_VERSI_OFFLINE_DATUM    int64
86        D19_VERSI_ONLINE_DATUM    int64
87     D19_VERSI_ONLINE_QUOTE_12  float64
88            D19_VERSICHERUNGEN    int64
89             D19_VOLLSORTIMENT    int64
90             D19_WEIN_FEINKOST    int64
91                      DSL_FLAG  float64
92          EINGEZOGENAM_HH_JAHR  float64
93                      EWDICHTE  float64
94                FINANZ_ANLEGER    int64
95              FINANZ_HAUSBAUER   

In [359]:
def fill_na_with_mean_and_convert(df, exclude_cols=None):
    """
    Fills NaN values in numeric columns with the mean and converts columns to int.
    
    Parameters:
    df (pd.DataFrame): The DataFrame to process.
    exclude_cols (list): A list of columns to exclude from processing.
    
    Returns:
    pd.DataFrame: The DataFrame with NaNs filled and columns converted to int.
    """
    if exclude_cols is None:
        exclude_cols = []

    # Step 1: Filter columns with dtype float or int, excluding specified columns
    filtered_columns = df.select_dtypes(include=['float', 'int']).drop(columns=exclude_cols, errors='ignore')

    # Step 2: Fill NaN values with the mean of each column
    filled_columns = filtered_columns.fillna(filtered_columns.mean())

    # Step 3: Convert columns to int
    filled_columns = filled_columns.astype(int)

    # Step 4: Update the original DataFrame
    df.update(filled_columns)

    return df


In [360]:
azdias = fill_na_with_mean_and_convert(azdias, exclude_cols=['LNR'])


In [361]:

customers = fill_na_with_mean_and_convert(customers, exclude_cols=['LNR','CUSTOMER_GROUP', 'ONLINE_PURCHASE', 'PRODUCT_GROUP'])

In [362]:
cn = create_null_table(customers)
an = create_null_table(azdias)

In [363]:
cn.head(20)

feature  null_count  percentage
128          OST_WEST_KZ       49927    0.260509
0                    LNR           0    0.000000
123          MOBI_RASTER           0    0.000000
115          KONSUMZELLE           0    0.000000
116      LP_FAMILIE_FEIN           0    0.000000
117      LP_FAMILIE_GROB           0    0.000000
118  LP_LEBENSPHASE_FEIN           0    0.000000
119  LP_LEBENSPHASE_GROB           0    0.000000
120       LP_STATUS_FEIN           0    0.000000
121       LP_STATUS_GROB           0    0.000000
122     MIN_GEBAEUDEJAHR           0    0.000000
124           MOBI_REGIO           0    0.000000
113           KOMBIALTER           0    0.000000
125     NATIONALITAET_KZ           0    0.000000
126    ONLINE_AFFINITAET           0    0.000000
127          ORTSGR_KLS9           0    0.000000
129           PLZ8_ANTG1           0    0.000000
130           PLZ8_ANTG2           0    0.000000
131           PLZ8_ANTG3           0    0.000000
132           PLZ8_ANTG4           0    0.000000

In [364]:
an.head(20)

feature  null_count  percentage
56   D19_LETZTER_KAUF_BRANCHE      257113    0.288495
128               OST_WEST_KZ       93148    0.104517
121            LP_STATUS_GROB           0    0.000000
113                KOMBIALTER           0    0.000000
114               KONSUMNAEHE           0    0.000000
115               KONSUMZELLE           0    0.000000
116           LP_FAMILIE_FEIN           0    0.000000
117           LP_FAMILIE_GROB           0    0.000000
118       LP_LEBENSPHASE_FEIN           0    0.000000
119       LP_LEBENSPHASE_GROB           0    0.000000
120            LP_STATUS_FEIN           0    0.000000
0                         LNR           0    0.000000
132                PLZ8_ANTG4           0    0.000000
122          MIN_GEBAEUDEJAHR           0    0.000000
123               MOBI_RASTER           0    0.000000
124                MOBI_REGIO           0    0.000000
125          NATIONALITAET_KZ           0    0.000000
126         ONLINE_AFFINITAET           0    0.000000
127               ORTSGR_KLS9           0    0.000000
129                PLZ8_ANTG1           0    0.000000

In [365]:
cn_obj = cn[cn['null_count']>0]
cn_obj_list = list(cn_obj['feature'])

In [366]:
an_obj = an[an['null_count']>0]
an_obj_list = list(an_obj['feature'])

In [367]:
filtered_cdt = cdt[cdt['feature'].isin(cn_obj_list)]
filtered_cdt

feature   dtype
128  OST_WEST_KZ  object

In [368]:
filtered_adt = adt[adt['feature'].isin(an_obj_list)]
filtered_adt

feature   dtype
56   D19_LETZTER_KAUF_BRANCHE  object
128               OST_WEST_KZ  object

In [369]:
for x in cn_obj_list:

    print(fetch_contains(x))

0    Information level    Attribute                       Description_x  \
2024               NaN  OST_WEST_KZ  flag indicating the former GDR/FRG   
2025               NaN  OST_WEST_KZ  flag indicating the former GDR/FRG   
2026               NaN  OST_WEST_KZ  flag indicating the former GDR/FRG   

0    Additional notes                       Description_y Value     Meaning  
2024              NaN  flag indicating the former GDR/FRG    -1     unknown  
2025              NaN  flag indicating the former GDR/FRG     O  East (GDR)  
2026              NaN  flag indicating the former GDR/FRG     W  West (FRG)  


In [370]:
fetch_contains('OST_WEST_KZ')

0    Information level    Attribute                       Description_x  \
2024               NaN  OST_WEST_KZ  flag indicating the former GDR/FRG   
2025               NaN  OST_WEST_KZ  flag indicating the former GDR/FRG   
2026               NaN  OST_WEST_KZ  flag indicating the former GDR/FRG   

0    Additional notes                       Description_y Value     Meaning  
2024              NaN  flag indicating the former GDR/FRG    -1     unknown  
2025              NaN  flag indicating the former GDR/FRG     O  East (GDR)  
2026              NaN  flag indicating the former GDR/FRG     W  West (FRG)

In [371]:


# Define batch size
BATCH_SIZE = 10000

# Step 1: Convert non-string categorical columns to strings
def preprocess_categorical_columns(df):
    for col in df.select_dtypes(include=['object', 'number']).columns:
        df[col] = df[col].astype(str)
    return df

# Step 2: Define function to reverse one-hot encoding
def reverse_one_hot(df, categorical_columns):
    reversed_df = df.copy()
    for col in categorical_columns:
        one_hot_columns = [c for c in df.columns if c.startswith(col)]
        if one_hot_columns:
            # Add the original categorical values back
            reversed_df[col] = reversed_df[one_hot_columns].idxmax(axis=1).str.replace(f'{col}_', '')
            reversed_df = reversed_df.drop(columns=one_hot_columns)
    return reversed_df

# Step 3: Define the imputation function with batch processing
def impute_na_batch(df, categorical_columns, numeric_columns):
    # Preprocess categorical columns
    df = preprocess_categorical_columns(df)

    # One-hot encode with sparse output
    encoder = OneHotEncoder(sparse_output=True, handle_unknown='ignore')
    encoded_data = encoder.fit_transform(df[categorical_columns])

    # Save the one-hot encoded column names
    encoded_column_names = encoder.get_feature_names_out(categorical_columns)

    # Convert numeric data to float explicitly to prevent type issues
    numeric_data = df[numeric_columns].astype(float).to_numpy()
    
    # Combine encoded categorical data with numeric data using hstack for sparse matrices
    combined_data = hstack([csr_matrix(numeric_data), encoded_data])

    # Apply KNN Imputation on combined sparse matrix data
    imputer = KNNImputer(n_neighbors=3)
    imputed_data = imputer.fit_transform(combined_data.toarray())

    # Convert imputed data back to DataFrame
    df_imputed = pd.DataFrame(imputed_data, columns=list(numeric_columns) + list(encoded_column_names))

    # Reverse one-hot encoding for categorical columns
    df_reversed = reverse_one_hot(df_imputed, categorical_columns)

    return df_reversed

# Step 4: Process the DataFrame in batches
def process_in_batches(df, batch_size):
    # Identify categorical and numeric columns
    categorical_columns = df.select_dtypes(include='object').columns
    numeric_columns = df.select_dtypes(exclude='object').columns
    
    batch_results = []
    for i in range(0, len(df), batch_size):
        batch = df.iloc[i:i + batch_size]
        imputed_batch = impute_na_batch(batch, categorical_columns, numeric_columns)
        batch_results.append(imputed_batch)

    # Concatenate all batches into a single DataFrame
    return pd.concat(batch_results, ignore_index=True)

In [372]:
fill_customers = process_in_batches(customers, BATCH_SIZE)
assert fill_customers.isna().any().sum() == 0

/var/folders/df/vskq6r65025_c31r_18tdcpr0000gn/T/ipykernel_63399/3184436992.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col] = df[col].astype(str)
/var/folders/df/vskq6r65025_c31r_18tdcpr0000gn/T/ipykernel_63399/3184436992.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col] = df[col].astype(str)
/var/folders/df/vskq6r65025_c31r_18tdcpr0000gn/T/ipykernel_63399/3184436992.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_ind

In [373]:
azdias_1 = azdias[:200000]

fill_azdias_1 = process_in_batches(azdias_1, BATCH_SIZE)


/var/folders/df/vskq6r65025_c31r_18tdcpr0000gn/T/ipykernel_63399/3184436992.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col] = df[col].astype(str)
/var/folders/df/vskq6r65025_c31r_18tdcpr0000gn/T/ipykernel_63399/3184436992.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col] = df[col].astype(str)
/var/folders/df/vskq6r65025_c31r_18tdcpr0000gn/T/ipykernel_63399/3184436992.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_ind

In [374]:
assert fill_azdias_1.isna().any().sum() == 0

In [ ]:
azdias_2 = azdias[200000:500000]

fill_azdias_2 = process_in_batches(azdias_2, BATCH_SIZE)

/var/folders/df/vskq6r65025_c31r_18tdcpr0000gn/T/ipykernel_63399/3184436992.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col] = df[col].astype(str)
/var/folders/df/vskq6r65025_c31r_18tdcpr0000gn/T/ipykernel_63399/3184436992.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col] = df[col].astype(str)
/var/folders/df/vskq6r65025_c31r_18tdcpr0000gn/T/ipykernel_63399/3184436992.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_ind

In [ ]:
azdias_3 = azdias[500000:800000]

fill_azdias_3 = process_in_batches(azdias_3, BATCH_SIZE)

In [ ]:
azdias_4 = azdias[800000:]

fill_azdias_4 = process_in_batches(azdias_4, BATCH_SIZE)

In [ ]:
combined_azdias = pd.concat([fill_azdias_4,fill_azdias_3, fill_azdias_2, fill_azdias_1], ignore_index=True)

# Display the shape of the combined DataFrame
print(combined_azdias.shape)

# Optional: Display the first few rows of the combined DataFrame
print(combined_azdias.head())


In [ ]:
assert combined_azdias.isna().any().sum() == 0

In [ ]:
attributes

In [ ]:
attr = attributes.drop_duplicates(subset='Attribute')

attr

In [ ]:
fetch_contains('KBA05_GBZ')

In [ ]:
# Identify common features
common_features = set(combined_azdias.columns) & set(fill_customers.columns)
print("Common Features:", common_features)

# Statistical comparison for numerical features
for feature in common_features:
    if customers[feature].dtype in ['int64', 'float64']:  # Only numerical features
        print(f"\nComparing {feature}:")
        print("Customers Mean:", customers[feature].mean())
        print("AZDIAS Mean:", azdias[feature].mean())
        print("(C-A)Mean Diff:", (customers[feature].mean()) - (azdias[feature].mean()))


In [ ]:
fill_customers
combined_azdias

In [297]:
cat_col = fill_customers.select_dtypes(include='object').columns

In [300]:
cat_col

Index(['CAMEO_DEU_2015', 'CAMEO_DEUG_2015', 'CAMEO_INTL_2015',
       'D19_LETZTER_KAUF_BRANCHE', 'EINGEFUEGT_AM', 'OST_WEST_KZ',
       'PRODUCT_GROUP', 'CUSTOMER_GROUP'],
      dtype='object')

In [312]:
To Drop: CAMEO_DEU_2015
CAMEO_DEUG_2015 - change to int and settle (nan, X) as -1, maybe fill mean
CAMEO_INTL_2015 - change to int and settle (nan, XX) as -1, maybe fill mean
D19_LETZTER_KAUF_BRANCHE - review the nan value, then onehot encode
EINGEFUEGT_AM - drop
OST_WEST_KZ - change nan text to Null and fill nan (KNN impute), then onehotencode
PRODUCT_GROUP - onehotencode
CUSTOMER_GROUP - onehotencode


1. drop column CAMEO_DEU_2015, EINGEFUEGT_AM
2. Replace nan, X, XX with -1 (CAMEO_DEUG_2015,CAMEO_INTL_2015)
3. Change to int (CAMEO_DEUG_2015,CAMEO_INTL_2015)
4. Replace nan(str) with NULL (D19_LETZTER_KAUF_BRANCHE, OST_WEST_KZ)

4. Preprocessing KNN Impute (onehotencode and reverse) all of them

5. onehot encode PRODUCT_GROUP, CUSTOMER_GROUP, OST_WEST_KZ, D19_LETZTER_KAUF_BRANCHE
6. t-test and cohen's d



3. change dtype to int (CAMEO_DEUG_2015)


SyntaxError: invalid syntax (2086279797.py, line 1)

In [329]:
fill_customers['CAMEO_DEUG_2015'].value_counts()

CAMEO_DEUG_2015
nan    50428
2      17574
4      16458
6      14008
3      13585
1      12498
8       9716
5       8624
7       7878
2.0     5910
4.0     5606
3.0     4805
9       4731
6.0     4709
1.0     4280
8.0     3333
5.0     3042
7.0     2680
9.0     1661
X        126
Name: count, dtype: int64

In [304]:
fill_customers['CAMEO_DEUG_2015'].isna().sum()

0

## Part 1: Customer Segmentation Report

The main bulk of your analysis will come in this part of the project. Here, you should use unsupervised learning techniques to describe the relationship between the demographics of the company's existing customers and the general population of Germany. By the end of this part, you should be able to describe parts of the general population that are more likely to be part of the mail-order company's main customer base, and which parts of the general population are less so.

## Part 2: Supervised Learning Model

Now that you've found which parts of the population are more likely to be customers of the mail-order company, it's time to build a prediction model. Each of the rows in the "MAILOUT" data files represents an individual that was targeted for a mailout campaign. Ideally, we should be able to use the demographic information from each individual to decide whether or not it will be worth it to include that person in the campaign.

The "MAILOUT" data has been split into two approximately equal parts, each with almost 43 000 data rows. In this part, you can verify your model with the "TRAIN" partition, which includes a column, "RESPONSE", that states whether or not a person became a customer of the company following the campaign. In the next part, you'll need to create predictions on the "TEST" partition, where the "RESPONSE" column has been withheld.

In [ ]:
mailout_train = pd.read_csv('data/Udacity_MAILOUT_052018_TRAIN.csv', sep=';')

In [ ]:
mailout_test = pd.read_csv('data/Udacity_MAILOUT_052018_TEST.csv', sep=';')

In [ ]:


def preprocess_categorical_columns(df):
    # Convert non-string categorical columns to strings
    for col in df.select_dtypes(include=['object', 'number']).columns:
        df[col] = df[col].astype(str)  # Convert all entries to strings
    return df

def impute_na_with_pca(df, n_components=50):
    # Preprocess the DataFrame to ensure categorical columns are strings
    df = preprocess_categorical_columns(df)

    # Step 1: Identify categorical and numeric columns
    categorical_columns = df.select_dtypes(include='object').columns
    numeric_columns = df.select_dtypes(exclude='object').columns

    # One-hot encode categorical columns with sparse matrix
    encoder = OneHotEncoder(sparse_output=True, handle_unknown='ignore')
    encoded_data = encoder.fit_transform(df[categorical_columns])

    # Combine encoded categorical data with numeric data
    numeric_data = df[numeric_columns].to_numpy()
    combined_data = csr_matrix(pd.concat([pd.DataFrame(numeric_data), pd.DataFrame.sparse.from_spmatrix(encoded_data)], axis=1))

    # Apply PCA for dimensionality reduction
    pca = PCA(n_components=n_components)
    reduced_data = pca.fit_transform(combined_data.toarray())

    # Step 2: Apply KNN Imputation on reduced data
    imputer = KNNImputer(n_neighbors=1)
    imputed_data = imputer.fit_transform(reduced_data)

    # Step 3: Reverse PCA transformation to get data back to original feature space
    imputed_data_original_space = pca.inverse_transform(imputed_data)

    # Convert imputed data back to DataFrame with original column names
    df_imputed = pd.DataFrame(imputed_data_original_space, columns=list(numeric_columns) + list(encoder.get_feature_names_out(categorical_columns)))

    # Step 4: Reverse one-hot encoding for categorical columns
    df_reversed = df_imputed.copy()
    for col in categorical_columns:
        one_hot_cols = [c for c in df_imputed.columns if c.startswith(col)]
        if one_hot_cols:
            df_reversed[col] = df_reversed[one_hot_cols].idxmax(axis=1).str.replace(f'{col}_', '')
            df_reversed = df_reversed.drop(columns=one_hot_cols)

    return df_reversed

# Example usage
imputed_customers = impute_na_with_pca(customers, n_components=50)
print(imputed_customers.isna().sum())


In [ ]:


# Define batch size
BATCH_SIZE = 10000

# Step 1: Convert non-string categorical columns to strings
def preprocess_categorical_columns(df):
    for col in df.select_dtypes(include=['object', 'number']).columns:
        df[col] = df[col].astype(str)
    return df

# Step 2: Define function to reverse one-hot encoding
def reverse_one_hot(df, categorical_columns):
    reversed_df = df.copy()
    for col in categorical_columns:
        one_hot_columns = [c for c in df.columns if c.startswith(col)]
        if one_hot_columns:
            # Add the original categorical values back
            reversed_df[col] = reversed_df[one_hot_columns].idxmax(axis=1).str.replace(f'{col}_', '')
            reversed_df = reversed_df.drop(columns=one_hot_columns)
    return reversed_df

# Step 3: Define the imputation function with batch processing
def impute_na_batch(df, categorical_columns, numeric_columns):
    # Preprocess categorical columns
    df = preprocess_categorical_columns(df)

    # One-hot encode with sparse output
    encoder = OneHotEncoder(sparse_output=True, handle_unknown='ignore')
    encoded_data = encoder.fit_transform(df[categorical_columns])

    # Save the one-hot encoded column names
    encoded_column_names = encoder.get_feature_names_out(categorical_columns)

    # Convert numeric data to float explicitly to prevent type issues
    numeric_data = df[numeric_columns].astype(float).to_numpy()
    
    # Combine encoded categorical data with numeric data using hstack for sparse matrices
    combined_data = hstack([csr_matrix(numeric_data), encoded_data])

    # Apply KNN Imputation on combined sparse matrix data
    imputer = KNNImputer(n_neighbors=1)
    imputed_data = imputer.fit_transform(combined_data.toarray())

    # Convert imputed data back to DataFrame
    df_imputed = pd.DataFrame(imputed_data, columns=list(numeric_columns) + list(encoded_column_names))

    # Reverse one-hot encoding for categorical columns
    df_reversed = reverse_one_hot(df_imputed, categorical_columns)

    return df_reversed

# Step 4: Process the DataFrame in batches
def process_in_batches(df, batch_size):
    # Identify categorical and numeric columns
    categorical_columns = df.select_dtypes(include='object').columns
    numeric_columns = df.select_dtypes(exclude='object').columns
    
    batch_results = []
    for i in range(0, len(df), batch_size):
        batch = df.iloc[i:i + batch_size]
        imputed_batch = impute_na_batch(batch, categorical_columns, numeric_columns)
        batch_results.append(imputed_batch)

    # Concatenate all batches into a single DataFrame
    return pd.concat(batch_results, ignore_index=True)


In [ ]:
# Example usage
imputed_azdias = impute_na_with_pca(azdias, n_components=50)
print(imputed_azdias.isna().sum())

In [ ]:
# Run the batch processing function on the 'customers' dataset
fill_customers = process_in_batches(customers, BATCH_SIZE)
print(fill_customers.isna().sum())

fill_customers.isna().sum()


In [ ]:
assert fill_mini_azdias.shape == mini_azdias.shape